# Lecture 3. Python Basics III: EXERCISES

## Photovoltaic (PV) System Monitoring

**Context:** You are working as a software engineer for a renewable energy company. Your task is to develop the backend logic for a solar park monitoring system. The system receives raw data logs from sensors, and you need to:

1. Calculate physical metrics (Power).

2. Assess safety status (Logic).

3. Parse raw text data into Python objects (String Handling).

4. Process large log files automatically (File I/O).

We will build this system step-by-step.

## Exercise 1: The Physics Calculation
**Goal**: Create a simple "helper function" that performs a specific calculation. In DC circuits, electrical power $P$ (in Watts) is calculated as Voltage $U$ multiplied by Current $I$.

**Task**: Define a function called calculate_power.

`Parameters`: voltage (float), current (float).

`Return`: The calculated power as a float, rounded to 2 decimal places.

**Hints**: For rounding use the standard buildin function `round()`. Research the syntax of the function in the internet or by hovering over the function to see the code annotation.

In [ ]:
# Define the function calculate_power here
    """
    Calculates electrical power P = U * I.
    Returns the result rounded to 2 decimal places.
    """
    # YOUR CODE STARTS HERE

In [ ]:
# solution
def calculate_power(voltage, current):
    """
    Calculates electrical power P = U * I.
    Returns the result rounded to 2 decimal places.
    """
    power = voltage*current # Calculater Power
    power = round(power, 2) # Round to two places
    return power

Test your function:

In [ ]:
# Test cases
p1 = calculate_power(230.5, 4.2)
p2 = calculate_power(12.0, 0.5)

print(f"Test 1 (Expected ~968.1): {p1}")
print(f"Test 2 (Expected 6.0): {p2}")

## Exercise 2: Safety Check Logic

**Goal**: Implement a function that checks if the operating condition is within the systems operating range.

A raw power value isn't enough; we need to know if the system is safe. Therefore we need to implement a function that checks wether the current operation conditions are within the systems safety margins. If not it should return a safety warning. Reuse the previously defined function to calculate the power.

**Task**: Define a function called `check_safety_status`.

`Parameters`: voltage, current, max_power (for max_power set a default value of 1000.0 Watts).

**Logic**:

Voltage Check: If voltage is greater than 400.0 V, `return` the string "CRITICAL: OVERVOLTAGE".

Power Calculation: Inside this function, call your calculate_power(voltage, current) function from Exercise 1 to get the actual wattage.

Power Check: If the calculated power is greater than max_power, `return` "WARNING: OVERPOWER".

Else: `return` "OK".

In [ ]:
# Define the function here
    """
    Determines if the sensor readings are within safe limits.
    Uses calculate_power() internally.
    """
    # Your code goes here

In [ ]:
# Solution
def check_safety_status(voltage, current, max_power = 1000.0):
    """
    Determines if the sensor readings are within safe limits.
    Uses calculate_power() internally.
    """
    if voltage > 400.0:
        return "CRITICAL: OVERVOLTAGE"
    
    power = calculate_power(voltage=voltage, current=current)

    if power > max_power:
        return "WARNING: OVERPOWER"
    
    return "OK"


Test your logic:

In [ ]:
print(check_safety_status(230, 2))              # Expected: OK
print(check_safety_status(450, 1))              # Expected: CRITICAL: OVERVOLTAGE
print(check_safety_status(230, 10))             # Expected: WARNING: OVERPOWER (2300W > 1000W)
print(check_safety_status(230, 10, max_power=3000)) # Expected: OK (Custom limit)

## Exercise 3: Parse a Log Message

**Goal:** Write a dedicated function to parse raw text lines into usable Python objects. You will use the Pyhon standard module: **`datetime`**. For more information on the `datetime` module, lookup the modules syntax in the Python documentation.

Data usually comes in messy text formats. A single line in our log file looks like this:
`"2025-10-25 14:30:00;230.5;4.2"`
*(Format: Timestamp;Voltage;Current)*

**Task:**

1.  **Import** the `datetime` class from the `datetime` module.
2.  Define a function `parse_log_line(line)`, which receives a single line of our logfile as a parameter.
3.  **Split the Input:** Split the line by the semicolon `;`.
4.  **Convert Time:** Use `datetime.strptime(date_string, "%Y-%m-%d %H:%M:%S")` to convert the first part into a datetime object.
5.  **Convert Numbers:** Convert the voltage and current parts to `float`.
6.  **Return:** A `tuple` containing `(datetime_object, voltage, current)`.

In [ ]:
# 1. Import the necessary module

# Define your function here
    """
    Parses a raw CSV-style line into usable Python objects.
    Input: "2025-10-25 14:30:00;230.5;4.2"
    Returns: (datetime_object, voltage_float, current_float)
    """

In [ ]:
#solution

from datetime import datetime

def parse_log_line(line: str):
    """
    Parses a raw CSV-style line into usable Python objects.
    Input: "2025-10-25 14:30:00;230.5;4.2"
    Returns: (datetime_object, voltage_float, current_float)
    """
    #clean the string and split it
    split_log = line.split(";")

    date = datetime.strptime(split_log[0], "%Y-%m-%d %H:%M:%S")

    voltage_float = float(split_log[1])
    current_float = float(split_log[2])

    return (date, voltage_float, current_float)

Test your function:

In [ ]:
# --- Test Area ---
test_line = "2025-10-25 14:30:00;230.5;4.2"
parsed_data = parse_log_line(test_line)

print(f"Input Line: {test_line}")
print(f"Parsed Data: {parsed_data}")

# Simple check to see if the first element is actually a datetime object
if parsed_data:
    print(f"Type of first element: {type(parsed_data[0])}")

## Exercise 4: The Main Processing Loop (File I/O & Orchestration)

**Goal:** Bring it all together! Read a file, parse it, check safety, and report results.

You will write a function that automates the whole process by using the tools you built in Exercises 1, 2, and 3.

### 4.1 Setup: Create Dummy Data
**Action:** Run the code cell below **once** to create the file `pv_sensor_log.txt` in your current folder. This simulates the data coming from the sensors.

In [ ]:
# --- SETUP: Run this cell once to create the dummy log file ---
log_content = """Timestamp;Voltage;Current
2025-11-01 08:00:00;230.1;2.0
2025-11-01 08:15:00;229.8;2.1
2025-11-01 08:30:00;405.2;0.0
2025-11-01 08:45:00;230.0;5.5
2025-11-01 09:00:00;229.5;2.0"""

with open("pv_sensor_log.txt", "w") as f:
    f.write(log_content)
    
print("File 'pv_sensor_log.txt' created successfully. Proceed to 4.2!")

### 4.2 Implement the File Processor

**Task:** Define the function `process_log_file(filename)`.

1.  **Open** the file using `with open(...)` in read mode.
2.  **Read** all lines and iterate through them.
    * *Important:* Skip the first line (the header)!
3.  **Process** inside the loop:
    * **Step A:** Call `parse_log_line(line)` (from Ex 3) to get the data variables (`dt`, `voltage`, `current`).
    * **Step B:** Call `check_safety_status(...)` (from Ex 2) to get the status string.
    * **Step C (Output):** Print the time and status.
        * If Status is "OK", print a normal info message. format: "[time] System Normal."
        * If Status is not okay, print an alert.          format: "[time] ALERT: status, (V=voltage, I=current)"
        * *Bonus:* Use `dt_object.strftime("%H:%M:%S")` to print a clean time format.

In [ ]:
# Define your function here
    print(f"--- Analyzing {filename} ---")

    print(f"--- Analysis complete ---")

# --- Test Area ---
# This will run your function on the file we created in 4.1
process_log_file("pv_sensor_log.txt")

In [ ]:
# Solution
def process_log_file(filename):
    print(f"--- Analyzing {filename} ---")
    header = True

    with open(filename, "r") as log:
        log_file = log.readlines()

    for log_line in log_file[1:]:
        datum, voltage, current = parse_log_line(log_line)
        time = datum.strftime("%H:%M:%S")
        status = check_safety_status(voltage=voltage, current=current)

        if status == "OK":
            print(f"[{time}] System nominal.")
        else:
            print(f"[{time}] ALERT: {status}, (V={voltage}, I={current})")

    print(f"--- Analysis complete ---")

# --- Test Area ---
# This will run your function on the file we created in 4.1
process_log_file("pv_sensor_log.txt")